In [17]:
import fiftyone as fo
import fiftyone.brain as fob
import numpy as np
from glob import glob
import json
import os

In [18]:
dataset = fo.Dataset.from_images_dir('data', name=None, tags=None, recursive=True)

 100% |███████████| 106589/106589 [37.4s elapsed, 0s remaining, 2.2K samples/s]      


INFO:eta.core.utils: 100% |███████████| 106589/106589 [37.4s elapsed, 0s remaining, 2.2K samples/s]      


In [19]:
session = fo.launch_app(dataset, auto=False)
# # http://localhost:5151

Session launched. Run `session.show()` to open the App in a cell output.


INFO:fiftyone.core.session.session:Session launched. Run `session.show()` to open the App in a cell output.


In [20]:
session

Dataset:          2024.09.14.13.30.38
Media type:       image
Num samples:      106589
Selected samples: 0
Selected labels:  0
Session URL:      http://localhost:5151/

In [21]:
import os
import csv
def format_frame_id(frame_id):
    return str(frame_id).zfill(3)

metadata_dir = 'media-info'
# Đọc các file CSV và tạo dictionary ánh xạ
frame_idx_map = {}
pts_time_map = {}

csv_folder = 'map-keyframes'  # Thay đổi đường dẫn này nếu cần

for csv_file in os.listdir(csv_folder):
    if csv_file.endswith('.csv'):
        video_name = os.path.splitext(csv_file)[0]
        frame_idx_map[video_name] = {}
        pts_time_map[video_name] = {}
        with open(os.path.join(csv_folder, csv_file), 'r') as f:
            csv_reader = csv.reader(f)
            next(csv_reader)  # Bỏ qua header
            for row in csv_reader:
                frame_id = format_frame_id(int(row[0]))
                frame_idx = int(row[3])
                pts_time = float(row[1])
                frame_idx_map[video_name][frame_id] = frame_idx
                pts_time_map[video_name][frame_id] = pts_time


In [22]:
frame_idx_map

{'L01_V001': {'001': 0,
  '002': 125,
  '003': 300,
  '004': 434,
  '005': 467,
  '006': 597,
  '007': 717,
  '008': 877,
  '009': 893,
  '010': 1053,
  '011': 1218,
  '012': 1384,
  '013': 1558,
  '014': 1714,
  '015': 1832,
  '016': 2007,
  '017': 2109,
  '018': 2255,
  '019': 2428,
  '020': 2517,
  '021': 2668,
  '022': 2840,
  '023': 2927,
  '024': 3003,
  '025': 3117,
  '026': 3292,
  '027': 3417,
  '028': 3567,
  '029': 3742,
  '030': 3867,
  '031': 3960,
  '032': 4120,
  '033': 4212,
  '034': 4235,
  '035': 4362,
  '036': 4526,
  '037': 4682,
  '038': 4857,
  '039': 4955,
  '040': 5057,
  '041': 5183,
  '042': 5308,
  '043': 5433,
  '044': 5558,
  '045': 5658,
  '046': 5749,
  '047': 5924,
  '048': 5999,
  '049': 6174,
  '050': 6344,
  '051': 6430,
  '052': 6520,
  '053': 6656,
  '054': 6686,
  '055': 6844,
  '056': 6898,
  '057': 7000,
  '058': 7075,
  '059': 7125,
  '060': 7154,
  '061': 7222,
  '062': 7261,
  '063': 7362,
  '064': 7531,
  '065': 7612,
  '066': 7681,
  '067': 

In [23]:
for sample in dataset:
    _, sample['video'], sample['frameid'] = sample['filepath'][:-4].rsplit('\\', 2)
    id = sample['video']
    sample['frame_idx'] = (frame_idx_map[id])[sample['frameid']]
    sample['pts_time'] = (pts_time_map[id])[sample['frameid']]
    print(sample["pts_time"])
    metadata_file = os.path.join(metadata_dir, id + ".json")
    if os.path.exists(metadata_file):
        # Load the metadata from the JSON file
        with open(metadata_file, "r") as f:
            metadata = json.load(f)
        
    # Create a VideoMetadata object if you're dealing with video frames
    publish_date = metadata.get("publish_date", None)
    url  = metadata.get("watch_url", None)
    # Alternatively, for images, use fo.ImageMetadata(**metadata)
    if publish_date and url:
        sample["url"] = url
        sample["date"] = publish_date


    # Save the sample to update it in the dataset
    sample.save()

0.0
5.0
12.0
17.4
18.68
23.88
28.68
35.12
35.72
42.12
48.72
55.36
62.32
68.56
73.32
80.32
84.36
90.2
97.12
100.68
106.72
113.6
117.08
120.12
124.68
131.68
136.68
142.68
149.68
154.68
158.4
164.8
168.48
169.4
174.48
181.04
187.28
194.28
198.2
202.28
207.32
212.32
217.32
222.32
226.32
229.96
236.96
239.96
246.96
253.76
257.2
260.8
266.28
267.44
273.76
275.96
280.0
283.0
285.0
286.16
288.88
290.44
294.48
301.28
304.48
307.28
311.32
314.32
319.6
326.6
331.28
335.48
339.8
345.12
351.8
355.48
359.48
362.76
367.92
369.24
372.0
376.48
382.04
386.8
393.8
399.8
405.8
411.28
416.2
421.16
426.16
432.16
439.16
442.2
446.32
450.48
456.8
462.16
467.24
472.0
476.2
480.16
487.16
490.72
495.48
500.8
503.8
509.24
513.48
516.2
518.8
524.76
527.8
534.64
539.48
542.32
544.32
549.16
551.48
555.76
560.52
563.76
565.08
569.8
576.32
582.72
589.72
593.72
597.72
604.56
611.04
614.2
616.4
620.6
623.24
625.84
628.84
631.68
635.68
638.68
643.68
650.68
657.68
664.68
668.6
675.44
679.84
684.2
687.56
694.56
697.56
703.

In [24]:
all_keyframe = glob('data\\*\\*.jpg')
video_keyframe_dict = {}
all_video = glob('data\\*')
all_video = [v.rsplit('\\',1)[-1] for v in all_video]


In [25]:
for kf in all_keyframe:
    _, vid, kf = kf[:-4].rsplit('\\',2)
    if vid not in video_keyframe_dict.keys():
        video_keyframe_dict[vid] = [kf]
    else:
        video_keyframe_dict[vid].append(kf)

In [26]:
for k,v in video_keyframe_dict.items():
    video_keyframe_dict[k] = sorted(v)

In [27]:
embedding_dict = {}
for v in all_video:
    clip_path = f'clip-features-32\\{v}.npy'
    a = np.load(clip_path)
    embedding_dict[v] = {}
    for i,k in enumerate(video_keyframe_dict[v]):
        embedding_dict[v][k] = a[i]


In [12]:
clip_embeddings = []
for sample in dataset:
    clip_embedding = embedding_dict[sample['video']][sample['frameid']]
    clip_embeddings.append(clip_embedding)


In [14]:
fob.compute_similarity(
    dataset,
    model="open-clip-torch",      # store model's name for future use
    embeddings=clip_embeddings,          # precomputed image embeddings
    brain_key="img_sim",
)

In [ ]:
# fob.compute_similarity(
#     dataset,
#     model="open-clip-torch",
#     embeddings=clip_embeddings,
#     brain_key="img_sim",
#     metric="cosine",
# )
